In [ ]:
import pandas as pd
import plotly.express as px

# --- Rutas de los archivos de entrada ---
SELLIN_PATH = 'https://storage.googleapis.com/open-courses/austral2025-af91/labo3v/sell-in.txt.gz'
PRODUCTOS_PATH = 'https://storage.googleapis.com/open-courses/austral2025-af91/labo3v/tb_productos.txt'
STOCKS_PATH = 'https://storage.googleapis.com/open-courses/austral2025-af91/labo3v/tb_stocks.txt'
PRODUCTS_TO_PREDICT_PATH = 'https://storage.googleapis.com/open-courses/austral2025-af91/labo3v/product_id_apredecir201912.txt'

# --- Cargando los datasets ---
print("Cargando dataset de Sell-In...")
sellin_df = pd.read_csv(SELLIN_PATH, sep='\t', compression='gzip',
                          dtype={'periodo': str, 'customer_id': str, 'product_id': str})
print(f"Sell-In cargado. Dimensiones: {sellin_df.shape}")

print("\nCargando dataset de Productos...")
productos_df = pd.read_csv(PRODUCTOS_PATH, sep='\t', dtype={'product_id': str})
print(f"Productos cargado. Dimensiones: {productos_df.shape}")

print("\nCargando dataset de Stocks...")
stocks_df = pd.read_csv(STOCKS_PATH, sep='\t', dtype={'periodo': str, 'product_id': str})
print(f"Stocks cargado. Dimensiones: {stocks_df.shape}")

print("\nCargando dataset de IDs de Productos a Predecir...")
productos_a_predecir_df = pd.read_csv(PRODUCTS_TO_PREDICT_PATH, sep='\t', dtype={'product_id': str})
print(f"IDs a predecir cargado. Dimensiones: {productos_a_predecir_df.shape}")

# --- Realizando los joins ---
print("\n--- Realizando Joins ---")
sellin_prod_df = pd.merge(sellin_df, productos_df, on='product_id', how='left')
all_chunk_df = pd.merge(sellin_prod_df, stocks_df, on=['periodo', 'product_id'], how='left')
print(f"Joins completados. Dimensiones de all_chunk_df: {all_chunk_df.shape}")

# --- Convirtiendo 'periodo' a datetime ---
print("\nConvirtiendo columna 'periodo' a datetime...")
all_chunk_df['periodo'] = pd.to_datetime(all_chunk_df['periodo'], format='%Y%m', errors='coerce')
print("Conversión completada.")

# --- Filtrado inicial por productos a predecir ---
all_chunk_depurado_df = all_chunk_df[
    all_chunk_df['product_id'].isin(productos_a_predecir_df['product_id'])
].copy()
print(f"Filtrado de IDs a predecir completado. Dimensiones: {all_chunk_depurado_df.shape}")

# --- Filtrado del rango de fechas ---
start_date = pd.to_datetime('2017-01-01')
end_date   = pd.to_datetime('2019-12-31')
df_filtered = all_chunk_depurado_df[
    (all_chunk_depurado_df['periodo'] >= start_date) &
    (all_chunk_depurado_df['periodo'] <= end_date)
].copy()

# --- Agregando ventas (tn) por periodo, producto y cliente ---
df_agg = df_filtered.groupby(['periodo', 'product_id', 'customer_id'])['tn'].sum().reset_index()

# --- Seleccionar los primeros 10 productos y 10 clientes (ordenados por código) ---
top_products = sorted(df_agg['product_id'].unique())[:10]
top_customers = sorted(df_agg['customer_id'].unique())[:10]
df_subset = df_agg[
    (df_agg['product_id'].isin(top_products)) &
    (df_agg['customer_id'].isin(top_customers))
]

# --- Determinar el máximo de tn en el subconjunto para fijar el eje Y ---
max_tn_subset = df_subset['tn'].max()

# --- Creación del gráfico: Facet grid con productos en filas y clientes en columnas ---
fig_subset = px.line(
    df_subset,
    x='periodo',
    y='tn',
    facet_row='product_id',
    facet_col='customer_id',
    title='Series Temporales de Ventas (tn) para 10 Productos x 10 Clientes'
)

# Configuramos los ejes: Y desde 0 hasta el máximo global, X con rango fijo
fig_subset.update_yaxes(range=[0, max_tn_subset])
fig_subset.update_xaxes(range=[start_date, end_date])

# Simplificar etiquetas en cada subgráfico quitando prefijos de la anotación
fig_subset.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))

# Ajustamos tamaño del dashboard
fig_subset.update_layout(height=800, width=1200)

# Mostramos el gráfico
fig_subset.show()

Cargando dataset de Sell-In...
Sell-In cargado. Dimensiones: (2945818, 7)

Cargando dataset de Productos...
Productos cargado. Dimensiones: (1251, 7)

Cargando dataset de Stocks...
Stocks cargado. Dimensiones: (13691, 3)

Cargando dataset de IDs de Productos a Predecir...
IDs a predecir cargado. Dimensiones: (780, 1)

--- Realizando Joins ---
Joins completados. Dimensiones de all_chunk_df: (2945818, 14)

Convirtiendo columna 'periodo' a datetime...
Conversión completada.
Filtrado de IDs a predecir completado. Dimensiones: (2293481, 14)


In [ ]:
import pandas as pd
import plotly.express as px

# --- Filtrado del rango de fechas ---
start_date = pd.to_datetime('2017-01-01')
end_date   = pd.to_datetime('2019-12-31')
df_filtered = all_chunk_depurado_df[
    (all_chunk_depurado_df['periodo'] >= start_date) &
    (all_chunk_depurado_df['periodo'] <= end_date)
].copy()

# --- Agregar ventas mensuales por producto ---
# Agrupamos por 'periodo' y 'product_id' sumando la cantidad vendida ("tn")
df_product = df_filtered.groupby(['periodo', 'product_id'])['tn'].sum().reset_index()

# --- Selección de los primeros 20 productos (ordenados por código) ---
top_products_20 = sorted(df_product['product_id'].unique())[:20]
df_product_subset = df_product[df_product['product_id'].isin(top_products_20)]

#########################################################
# GRÁFICO 1: Ventas Acumuladas (Cumulative Sales)
#########################################################
# Ordenamos por periodo y calculamos el acumulado para cada producto
df_product_subset = df_product_subset.sort_values('periodo')
df_product_subset['cumulative_tn'] = df_product_subset.groupby('product_id')['tn'].cumsum()

# Determinamos el valor máximo acumulado para ajustar el eje Y
max_cumulative = df_product_subset['cumulative_tn'].max()

# Creamos el gráfico: cada fila representa un producto y se traza la serie acumulada
fig_cumulative = px.line(
    df_product_subset,
    x='periodo',
    y='cumulative_tn',
    facet_row='product_id',
    title='Ventas Acumuladas (tn) para los Primeros 20 Productos'
)

# Configuramos ejes: eje Y desde 0 hasta el máximo acumulado y eje X con el rango fijo
fig_cumulative.update_yaxes(range=[0, max_cumulative])
fig_cumulative.update_xaxes(range=[start_date, end_date])

# Simplificamos las anotaciones en cada facet (quitando la etiqueta "product_id=")
fig_cumulative.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))

# Ajustamos dimensiones del dashboard
fig_cumulative.update_layout(height=1200, width=800)
fig_cumulative.show()

#########################################################
# GRÁFICO 2: Ventas Mensuales (Raw Sales)
#########################################################
# Determinamos el valor máximo de ventas mensuales en el subconjunto para fijar el eje Y
max_monthly = df_product_subset['tn'].max()

# Creamos la gráfica de líneas no acumuladas, manteniendo la misma estructura de facetas
fig_raw = px.line(
    df_product_subset,
    x='periodo',
    y='tn',
    facet_row='product_id',
    title='Ventas Mensuales (tn) para los Primeros 20 Productos'
)
fig_raw.update_yaxes(range=[0, max_monthly])
fig_raw.update_xaxes(range=[start_date, end_date])
fig_raw.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
fig_raw.update_layout(height=1200, width=800)
fig_raw.show()

In [ ]:
# Para el gráfico de Ventas Mensuales:
fig_raw.update_layout(height=3800, width=800)  # Aumentamos el alto y ancho
fig_raw.show()

In [ ]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# --- SUPONEMOS QUE YA TENÉS EL DATAFRAME all_chunk_depurado_df ---
# Filtrado del rango de fechas
start_date = pd.to_datetime('2017-01-01')
end_date   = pd.to_datetime('2019-12-31')
df_filtered = all_chunk_depurado_df[
    (all_chunk_depurado_df['periodo'] >= start_date) &
    (all_chunk_depurado_df['periodo'] <= end_date)
].copy()

# --- Agrupación para obtener la información deseada por producto y mes ---
# Para cada 'product_id' y 'periodo', calculamos: media, mínimo, máximo y total de ventas (tn)
df_var = df_filtered.groupby(['product_id', 'periodo'])['tn'].agg(['mean', 'min', 'max', 'sum']).reset_index()
df_var.columns = ['product_id', 'periodo', 'mean', 'min_val', 'max_val', 'total']

# --- Selección de los primeros 20 productos ordenados por código ---
top_products_20 = sorted(df_var['product_id'].unique())[:20]
df_var_subset = df_var[df_var['product_id'].isin(top_products_20)].copy()

# --- Creación de la figura con subplots: 1 columna y 20 filas (una para cada producto) ---
num_products = len(top_products_20)
fig = make_subplots(
    rows=num_products, cols=1, shared_xaxes=True,
    subplot_titles=[f"Producto: {prod}" for prod in top_products_20]
)

# --- Para cada producto, agregamos las trazas:
#    - Una traza para el valor mínimo (línea inferior de la banda).
#    - Una traza para el valor máximo con 'fill="tonexty"' para sombrear el área entre el mínimo y el máximo.
#    - Una traza para la línea de la media.
#    - Una traza para la línea del total de ventas.  ---
for i, prod in enumerate(top_products_20):
    df_p = df_var_subset[df_var_subset['product_id'] == prod].sort_values('periodo')
    row_index = i + 1

    # Trazado del valor mínimo
    fig.add_trace(go.Scatter(
        x=df_p['periodo'],
        y=df_p['min_val'],
        mode='lines',
        line=dict(color='lightblue'),
        name='Mínimo',
        showlegend=(i == 0),
        legendgroup='MinMax'
    ), row=row_index, col=1)

    # Trazado del valor máximo con 'fill="tonexty"' para crear la banda
    fig.add_trace(go.Scatter(
        x=df_p['periodo'],
        y=df_p['max_val'],
        mode='lines',
        line=dict(color='lightblue'),
        fill='tonexty',  # rellena la zona entre esta traza y la anterior (mínimo)
        fillcolor='rgba(173,216,230,0.3)',
        name='Máximo',
        showlegend=(i == 0),
        legendgroup='MinMax'
    ), row=row_index, col=1)

    # Trazado de la media por cliente
    fig.add_trace(go.Scatter(
        x=df_p['periodo'],
        y=df_p['mean'],
        mode='lines',
        line=dict(color='orange', width=2),
        name='Media',
        showlegend=(i == 0),
        legendgroup='Media'
    ), row=row_index, col=1)

    # Trazado del total de ventas (de ese producto, sumado entre clientes)
    fig.add_trace(go.Scatter(
        x=df_p['periodo'],
        y=df_p['total'],
        mode='lines',
        line=dict(color='green', width=2, dash='dash'),
        name='Total',
        showlegend=(i == 0),
        legendgroup='Total'
    ), row=row_index, col=1)

# --- Ajustes generales del layout ---
fig.update_xaxes(range=[start_date, end_date])
fig.update_layout(
    height=4000,    # ajustar la altura para que cada fila tenga más espacio
    width=1400,
    title_text="Variación de Ventas por Cliente: Banda (mínimo-máximo), Media y Total por Producto (20 Productos)"
)

fig.show()

In [ ]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

# Filtrado del rango de fechas
start_date = pd.to_datetime('2017-01-01')
end_date   = pd.to_datetime('2019-12-31')
df_box = all_chunk_depurado_df[
    (all_chunk_depurado_df['periodo'] >= start_date) &
    (all_chunk_depurado_df['periodo'] <= end_date)
].copy()

# Agrupar por periodo y por cliente para obtener el total vendido a cada cliente en cada mes
df_client_sales = df_box.groupby(['periodo', 'customer_id'])['tn'].sum().reset_index()

# Calcular el total vendido mensual (suma de ventas de todos los clientes, para cada mes)
df_total_monthly = df_client_sales.groupby('periodo')['tn'].sum().reset_index()

# Crear el boxplot. Cada caja representa la distribución de las ventas totales por cliente en un mes,
# mostrando la mediana, los cuartiles y los outliers.
fig_box = px.box(
    df_client_sales,
    x='periodo',
    y='tn',
    points="outliers",
    title='Distribución del Total Vendido por Cliente por Mes'
)

# Agregar la línea con el total mensual de ventas para referencia.
fig_box.add_trace(
    go.Scatter(
        x=df_total_monthly['periodo'],
        y=df_total_monthly['tn'],
        mode='lines+markers',
        name='Total Ventas Mensuales',
        line=dict(color='green', dash='dash')
    )
)

# Ajustar dimensiones y rango de ejes para mejorar la visualización
fig_box.update_layout(height=800, width=1400)
fig_box.update_xaxes(range=[start_date, end_date])

fig_box.show()

In [ ]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

# --- Supongamos que ya disponés del DataFrame 'all_chunk_depurado_df'
#     y que la columna 'periodo' ya fue convertida a datetime.

# Filtrado del rango de fechas
start_date = pd.to_datetime('2017-01-01')
end_date   = pd.to_datetime('2019-12-31')
df_filtered = all_chunk_depurado_df[
    (all_chunk_depurado_df['periodo'] >= start_date) &
    (all_chunk_depurado_df['periodo'] <= end_date)
].copy()

# --- Agrupar a nivel de cliente, producto y periodo ---
# Esto te da la venta total (en tn) para cada cliente para un producto en un mes.
df_client = df_filtered.groupby(['product_id', 'periodo', 'customer_id'])['tn'].sum().reset_index()

# Seleccionar los primeros 20 productos (ordenados por código) para que la visualización sea manejable.
top_products = sorted(df_client['product_id'].unique())[:20]
df_client = df_client[df_client['product_id'].isin(top_products)].copy()

# --- Calcular el total de ventas de cada producto en cada mes (suma para todos los clientes)
df_total = df_client.groupby(['product_id', 'periodo'])['tn'].sum().reset_index()

# --- Creación del gráfico de boxplots por producto en un facet grid ---
# Cada facet (fila) corresponderá a un producto y los boxplots se muestran a lo largo de 'periodo'
fig = px.box(
    df_client,
    x='periodo',
    y='tn',
    facet_row='product_id',
    points="outliers",
    title='Distribución de Ventas por Cliente por Mes para los Primeros 20 Productos',
    labels={'tn': 'Ventas (tn)', 'periodo': 'Periodo'}
)

# --- Superponer la línea con el total de ventas ---
# Para cada producto, se añade una traza que conecta los totales mensuales (sumados entre clientes).
for prod in top_products:
    df_prod_total = df_total[df_total['product_id'] == prod].sort_values('periodo')
    # Recordá que en un facet grid con facet_row, la indexación de filas corresponde al orden
    # de los valores únicos en 'product_id'. Usamos la posición de 'prod' en 'top_products' para determinar la fila.
    row_index = top_products.index(prod) + 1  # +1 porque las filas se cuentan a partir de 1
    fig.add_trace(
        go.Scatter(
            x=df_prod_total['periodo'],
            y=df_prod_total['tn'],
            mode='lines+markers',
            line=dict(color='green', dash='dash'),
            name='Total Ventas' if prod == top_products[0] else None,
            showlegend=True if prod == top_products[0] else False
        ),
        row=row_index,
        col=1
    )

# --- Ajustes de layout para ampliar los diagramas ---
fig.update_layout(height=3000, width=1400)
fig.update_xaxes(range=[start_date, end_date])
fig.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))

fig.show()

In [ ]:
fig.update_yaxes(type="log")

In [ ]:
import pandas as pd
import plotly.express as px

# Supongamos que ya disponés del DataFrame 'all_chunk_depurado_df'
# y que la columna 'periodo' ya está convertida a datetime.

# Filtramos para el rango de fechas de interés:
start_date = pd.to_datetime('2017-01-01')
end_date   = pd.to_datetime('2019-12-31')
df_filtered = all_chunk_depurado_df[
    (all_chunk_depurado_df['periodo'] >= start_date) &
    (all_chunk_depurado_df['periodo'] <= end_date)
].copy()

# Agrupamos por producto, mes y cliente para tener la venta total de cada cliente para un producto en ese mes.
df_client = df_filtered.groupby(['product_id', 'periodo', 'customer_id'])['tn'].sum().reset_index()

# Calculamos el IQR de las ventas para cada producto en cada mes.
def iqr(x):
    return x.quantile(0.75) - x.quantile(0.25)

df_iqr = df_client.groupby(['product_id', 'periodo'])['tn'].agg(iqr).reset_index().rename(columns={'tn': 'IQR'})

# Seleccionamos, por ejemplo, los primeros 20 productos ordenados por código para facilitar la visualización.
top_products = sorted(df_iqr['product_id'].unique())[:20]
df_iqr_subset = df_iqr[df_iqr['product_id'].isin(top_products)].copy()

# Creamos una tabla pivote con productos en filas y periodos en columnas, cuyos valores sean el IQR.
pivot_iqr = df_iqr_subset.pivot(index='product_id', columns='periodo', values='IQR')
pivot_iqr = pivot_iqr.sort_index(axis=1)

# Convertimos las fechas de las columnas a un formato legible (por ejemplo, 'YYYY-MM').
x_labels = [d.strftime('%Y-%m') for d in pivot_iqr.columns]

# Generamos el heatmap con Plotly Express.
fig_heatmap = px.imshow(
    pivot_iqr,
    labels=dict(x="Periodo", y="Producto", color="IQR (tn)"),
    x=x_labels,
    y=pivot_iqr.index,
    aspect="auto",
    title="Mapa de Calor del IQR de Ventas por Cliente para cada Producto y Mes"
)

fig_heatmap.update_layout(width=1400, height=800)
fig_heatmap.show()

In [ ]:
import pandas as pd
import plotly.express as px

# Supongamos que 'all_chunk_depurado_df' ya está cargado y la columna 'periodo' es datetime

# 1. Filtrar el rango de fechas de interés
start_date = pd.to_datetime('2017-01-01')
end_date   = pd.to_datetime('2019-12-31')
df_filtered = all_chunk_depurado_df[(all_chunk_depurado_df['periodo'] >= start_date) &
                                    (all_chunk_depurado_df['periodo'] <= end_date)].copy()

# 2. Agrupar a nivel de producto, cliente y mes: total vendido en tn
df_grouped = df_filtered.groupby(['product_id', 'customer_id', 'periodo'])['tn'].sum().reset_index()

# 3. Seleccionar los Top 5 productos y Top 5 clientes (ordenados lexicográficamente)
top_products = sorted(df_grouped['product_id'].unique())[:5]
top_customers = sorted(df_grouped['customer_id'].unique())[:5]
df_subset = df_grouped[
    (df_grouped['product_id'].isin(top_products)) &
    (df_grouped['customer_id'].isin(top_customers))
].copy()

# 4. Completar la serie para cada combinación producto-cliente
all_periods = pd.date_range(start=start_date, end=end_date, freq='MS')  # Frecuencia mensual
all_combos = pd.MultiIndex.from_product([top_products, top_customers, all_periods],
                                          names=['product_id', 'customer_id', 'periodo'])
df_complete = pd.DataFrame(index=all_combos).reset_index()

# Combinar con el subset original (para incorporar meses sin ventas, que llenamos con 0)
df_merged = pd.merge(df_complete, df_subset,
                     on=['product_id', 'customer_id', 'periodo'], how='left')
df_merged['tn'] = df_merged['tn'].fillna(0)

# 5. Cuantización: Asignar a cada mes un bin en función de las ventas (bin de tamaño 10)
df_merged['bin'] = (df_merged['tn'] // 10) * 10

# 6. Graficar en un facet grid 5x5
fig = px.line(df_merged,
              x='periodo',
              y='bin',
              markers=True,
              facet_row='product_id',
              facet_col='customer_id',
              title='Serie de Ventas Cuantizadas (bin size=10) por Producto y Cliente (Top 5x5)',
              labels={'bin': 'Ventas (bin)', 'periodo': 'Periodo'})

# Ajustes en los ejes
fig.update_yaxes(tick0=0, dtick=10)
fig.update_xaxes(range=[start_date, end_date])
fig.update_layout(height=1200, width=1400)

# Simplificar las anotaciones de cada facet (quitamos "product_id=" o "customer_id=")
fig.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))

fig.show()

In [ ]:
import pandas as pd
import plotly.express as px

# --- 1. Filtrado y agregación de los datos ---
# Supongamos que ya disponemos del DataFrame 'all_chunk_depurado_df' con la columna 'periodo' en formato datetime.
start_date = pd.to_datetime('2017-01-01')
end_date   = pd.to_datetime('2019-12-31')
df_filtered = all_chunk_depurado_df[(all_chunk_depurado_df['periodo'] >= start_date) &
                                    (all_chunk_depurado_df['periodo'] <= end_date)].copy()

# Crear una columna con el formato "tn_YYYY_MM" para cada venta
df_filtered["year_month"] = df_filtered["periodo"].dt.strftime("tn_%Y_%m")

# Agrupar: obtener el total vendido (en toneladas) en cada mes para cada combinación de producto y cliente
df_agg = df_filtered.groupby(["product_id", "customer_id", "year_month"])["tn"].sum().reset_index()

# --- 2. Pivotar para tener la serie de tiempo en columnas ---
# Generamos la lista de columnas de la serie a partir de 2017 a 2019 (12 meses x 3 años = 36 columnas)
time_series_columns = [f"tn_{year}_{month:02d}" for year in range(2017, 2020) for month in range(1, 13)]

# Pivotamos: cada fila corresponderá a una combinación producto–cliente y las columnas a cada mes
df_pivot = df_agg.pivot_table(index=["product_id", "customer_id"],
                              columns="year_month", values="tn", aggfunc="sum")
# Nos aseguramos de tener todas las columnas, incluso si faltan (se llenarán con 0)
df_pivot = df_pivot.reindex(columns=time_series_columns)
df_pivot = df_pivot.fillna(0).reset_index()

# --- 3. Función para cuantizar la serie de tiempo ---
# Se usa la idea de la función que compartiste, cambiando el número de cuantiles a 10
def clean_data(df):
    # Definimos las columnas de la serie
    time_series_columns = [f"tn_{year}_{month:02d}" for year in range(2017, 2020) for month in range(1, 13)]
    # Para cada fila, usamos pd.qcut sobre el ranking de la serie
    df[time_series_columns] = df[time_series_columns].apply(
        lambda row: pd.qcut(row.rank(method="first"), q=10, labels=False), axis=1
    )
    return df

df_quantized = clean_data(df_pivot.copy())

# --- 4. Transformar a formato largo para graficar ---
df_long = df_quantized.melt(id_vars=["product_id", "customer_id"],
                             value_vars=time_series_columns,
                             var_name="Month", value_name="Quantile")

# --- 5. Filtrar las 5 combinaciones principales para una grilla 5x5 ---
# Por ejemplo, tomar los primeros 5 productos y los primeros 5 clientes (ordenados lexicográficamente)
top_products = sorted(df_long["product_id"].unique())[:5]
top_customers = sorted(df_long["customer_id"].unique())[:5]
df_long_subset = df_long[(df_long["product_id"].isin(top_products)) &
                         (df_long["customer_id"].isin(top_customers))].copy()

# --- 6. Graficar usando un gráfico de barras ---
fig = px.bar(df_long_subset,
             x="Month",
             y="Quantile",
             facet_row="product_id",
             facet_col="customer_id",
             title="Series Cuantizadas (q=10) de Ventas Totales por Producto y Cliente",
             labels={"Quantile": "Nivel Cuantizado", "Month": "Mes"},
             category_orders={"Month": time_series_columns})

# Ajuste del layout para mayor claridad
fig.update_layout(height=800, width=1200)
fig.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
fig.show()

In [ ]:
import pandas as pd
import plotly.express as px
import plotly.io as pio

# Restablecer el template por defecto
pio.templates.default = "plotly"

# --- 1. Filtrar el dataset por el rango de fechas de interés ---
start_date = pd.to_datetime('2017-01-01')
end_date   = pd.to_datetime('2019-12-31')
df_filtered = all_chunk_depurado_df[(all_chunk_depurado_df['periodo'] >= start_date) &
                                    (all_chunk_depurado_df['periodo'] <= end_date)].copy()

# --- 2. Agrupar los datos: total vendido (en toneladas) por producto, cliente y mes ---
df_grouped = df_filtered.groupby(['product_id', 'customer_id', 'periodo'])['tn'].sum().reset_index()

# --- 3. Completar la serie temporal para cada combinación producto-cliente ---
# Crear un rango de fechas mensuales
all_months = pd.date_range(start=start_date, end=end_date, freq='MS')

# Seleccionar un subconjunto manejable (por ejemplo, top 5 productos y top 5 clientes)
unique_products = sorted(df_grouped['product_id'].unique())[:5]
unique_customers = sorted(df_grouped['customer_id'].unique())[:5]

# Crear DataFrame con todas las combinaciones producto, cliente y mes
all_combinations = pd.MultiIndex.from_product(
    [unique_products, unique_customers, all_months],
    names=['product_id', 'customer_id', 'periodo']
).to_frame(index=False)

# Merge para incorporar datos reales y rellenar con 0 los meses sin ventas
df_complete = pd.merge(all_combinations, df_grouped, on=['product_id', 'customer_id', 'periodo'], how='left')
df_complete['tn'] = df_complete['tn'].fillna(0)

# --- 4. Graficar la serie de tiempo en un facet grid ---
fig = px.line(
    df_complete,
    x='periodo',
    y='tn',
    facet_row='product_id',
    facet_col='customer_id',
    title='Línea de Tiempo de Ventas (con ceros en los faltantes) por Producto y Cliente',
    labels={'tn': 'Ventas (tn)', 'periodo': 'Periodo'}
)

# Reiniciar y ajustar los ejes
fig.update_xaxes(range=[start_date, end_date])
fig.update_yaxes(rangemode="tozero", autorange=True)

# Actualizar el layout para "resetear" parámetros heredados
fig.update_layout(
    height=800,
    width=1200,
    template="plotly",
    title={'x': 0.5, 'xanchor': 'center'},
    showlegend=False
)

# Simplificar las anotaciones de cada subgráfico (quitar prefijos)
fig.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))

fig.show()

In [ ]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.io as pio
from statsmodels.tsa.seasonal import seasonal_decompose

# Restablecer el template por defecto para evitar configuraciones heredadas.
pio.templates.default = "plotly"

# ======================================================
# Paso 1: Preparar la serie completa por Producto-Cliente
# ======================================================
start_date = pd.to_datetime('2017-01-01')
end_date   = pd.to_datetime('2019-12-31')
df_filtered = all_chunk_depurado_df[
    (all_chunk_depurado_df['periodo'] >= start_date) &
    (all_chunk_depurado_df['periodo'] <= end_date)
].copy()

# Agrupar los datos: total vendido (en toneladas) por producto, cliente y mes.
df_grouped = df_filtered.groupby(['product_id', 'customer_id', 'periodo'])['tn'].sum().reset_index()

# Para efectos prácticos, seleccionamos un subconjunto manejable: los primeros 5 productos y los primeros 5 clientes.
unique_products = sorted(df_grouped['product_id'].unique())[:5]
unique_customers = sorted(df_grouped['customer_id'].unique())[:5]

# Crear un rango de meses completos (frecuencia mensual, MS indica el inicio del mes).
all_months = pd.date_range(start=start_date, end=end_date, freq='MS')

# Generar todas las combinaciones de producto, cliente y mes.
all_combinations = pd.MultiIndex.from_product(
    [unique_products, unique_customers, all_months],
    names=['product_id', 'customer_id', 'periodo']
).to_frame(index=False)

# Hacer merge para incorporar los datos reales y rellenar con 0 donde falten.
df_complete = pd.merge(all_combinations, df_grouped,
                       on=['product_id', 'customer_id', 'periodo'], how='left')
df_complete['tn'] = df_complete['tn'].fillna(0)

# ======================================================
# Paso 2: Descomponer la serie en sus componentes
# ======================================================
# Usaremos seasonal_decompose (modelo aditivo, period=12 para series mensuales).
decomp_results = []
grouped = df_complete.groupby(['product_id', 'customer_id'])
for (prod, cust), group in grouped:
    group_sorted = group.sort_values('periodo').copy()
    # Se requiere una serie suficientemente larga para la descomposición.
    if len(group_sorted) < 24:
        continue
    try:
        decomp = seasonal_decompose(group_sorted['tn'], model='additive', period=12, extrapolate_trend="freq")
    except Exception as ex:
        print(f"No se pudo descomponer para {prod} - {cust}: {ex}")
        continue
    dtemp = pd.DataFrame({
        'periodo': group_sorted['periodo'],
        'trend': decomp.trend,
        'seasonal': decomp.seasonal,
        'resid': decomp.resid
    })
    dtemp['product_id'] = prod
    dtemp['customer_id'] = cust
    decomp_results.append(dtemp)

if decomp_results:
    df_decomp = pd.concat(decomp_results, ignore_index=True)
else:
    print("No se realizó ninguna descomposición.")
    df_decomp = pd.DataFrame()

# ======================================================
# Paso 3: Graficar con ejes "liberados"
# ======================================================
# En este caso, "liberamos" los ejes dejando que Plotly ajuste los ticks de forma automática.

# Gráfico (A) - Componente Estacional
fig_seasonal = px.line(
    df_decomp,
    x="periodo",
    y="seasonal",
    facet_row="product_id",
    facet_col="customer_id",
    title="Componente Estacional (Estacionariedad) por Producto y Cliente",
    labels={"seasonal": "Estacional", "periodo": "Periodo"}
)

# Para el eje X fijamos el rango, pero no forzamos dtick ni formato; se dejan libres el resto
fig_seasonal.update_xaxes(range=[start_date, end_date])
# Dejamos el eje Y sin restricciones adicionales (aprovechando el ajuste automático)
fig_seasonal.update_yaxes(autorange=True)

fig_seasonal.update_layout(
    height=800,
    width=1200,
    template="plotly",
    title={'x': 0.5, 'xanchor': 'center'},
    showlegend=False,
    margin=dict(l=50, r=50, t=50, b=50)
)
fig_seasonal.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
fig_seasonal.show()

# Gráfico (B) - Componente de Tendencia
fig_trend = px.line(
    df_decomp,
    x="periodo",
    y="trend",
    facet_row="product_id",
    facet_col="customer_id",
    title="Componente de Tendencia por Producto y Cliente",
    labels={"trend": "Tendencia", "periodo": "Periodo"}
)
fig_trend.update_xaxes(range=[start_date, end_date])
fig_trend.update_yaxes(autorange=True)
fig_trend.update_layout(
    height=800,
    width=1200,
    template="plotly",
    title={'x': 0.5, 'xanchor': 'center'},
    showlegend=False,
    margin=dict(l=50, r=50, t=50, b=50)
)
fig_trend.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
fig_trend.show()

# Gráfico (C) - Componente de Ruido (Residuos)
fig_resid = px.line(
    df_decomp,
    x="periodo",
    y="resid",
    facet_row="product_id",
    facet_col="customer_id",
    title="Componente de Ruido (Residuos) por Producto y Cliente",
    labels={"resid": "Ruido", "periodo": "Periodo"}
)
fig_resid.update_xaxes(range=[start_date, end_date])
fig_resid.update_yaxes(autorange=True)
fig_resid.update_layout(
    height=800,
    width=1200,
    template="plotly",
    title={'x': 0.5, 'xanchor': 'center'},
    showlegend=False,
    margin=dict(l=50, r=50, t=50, b=50)
)
fig_resid.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
fig_resid.show()

In [ ]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.io as pio
from statsmodels.tsa.seasonal import seasonal_decompose

# Restablecemos el template por defecto para evitar configuraciones heredadas.
pio.templates.default = "plotly"

# -------------------------------
# Paso 1: Filtrado y agrupación a nivel de producto
# -------------------------------
start_date = pd.to_datetime('2017-01-01')
end_date   = pd.to_datetime('2019-12-31')
df_filtered = all_chunk_depurado_df[
    (all_chunk_depurado_df['periodo'] >= start_date) &
    (all_chunk_depurado_df['periodo'] <= end_date)
].copy()

# Agrupar por producto y mes (sumando ventas de todos los clientes)
df_grouped = df_filtered.groupby(['product_id', 'periodo'])['tn'].sum().reset_index()

# Para efectos prácticos, seleccionamos un subconjunto manejable: por ejemplo, los primeros 10 productos (o los que prefieras)
unique_products = sorted(df_grouped['product_id'].unique())[:10]

# Crear un rango de meses completos (usamos frecuencia 'MS' para indicar el inicio del mes)
all_months = pd.date_range(start=start_date, end=end_date, freq='MS')

# Crear un DataFrame con todas las combinaciones posibles de producto y mes para los productos seleccionados
all_combinations = pd.MultiIndex.from_product(
    [unique_products, all_months],
    names=['product_id', 'periodo']
).to_frame(index=False)

# Merge de las combinaciones con los datos reales y relleno con 0 para los meses sin ventas
df_complete = pd.merge(all_combinations, df_grouped, on=['product_id', 'periodo'], how='left')
df_complete['tn'] = df_complete['tn'].fillna(0)

# -------------------------------
# Paso 2: Descomposición de la serie para cada producto
# -------------------------------
# Usamos seasonal_decompose (modelo aditivo y period=12, ya que los datos son mensuales)
decomp_results = []
grouped = df_complete.groupby('product_id')
for prod, group in grouped:
    group_sorted = group.sort_values('periodo').copy()
    # Solo descomponemos si tenemos suficientes datos (por ej. al menos 24 puntos)
    if len(group_sorted) < 24:
        continue
    try:
        decomp = seasonal_decompose(group_sorted['tn'], model='additive', period=12, extrapolate_trend="freq")
    except Exception as ex:
        print(f"No se pudo descomponer para el producto {prod}: {ex}")
        continue
    dtemp = pd.DataFrame({
        'periodo': group_sorted['periodo'],
        'trend': decomp.trend,
        'seasonal': decomp.seasonal,
        'resid': decomp.resid
    })
    dtemp['product_id'] = prod
    decomp_results.append(dtemp)

if decomp_results:
    df_decomp = pd.concat(decomp_results, ignore_index=True)
else:
    print("No se realizó ninguna descomposición.")
    df_decomp = pd.DataFrame()

# -------------------------------
# Paso 3: Visualización (una fila por producto)
# -------------------------------
# Usamos un facet grid con facet_row para que cada fila sea un producto. No hay facet_col ya que la serie es a nivel de producto.

# (A) Gráfico de la componente estacional
fig_seasonal = px.line(
    df_decomp,
    x="periodo",
    y="seasonal",
    facet_row="product_id",
    title="Componente Estacional (Estacionariedad) por Producto",
    labels={"seasonal": "Estacional", "periodo": "Periodo"}
)
fig_seasonal.update_xaxes(range=[start_date, end_date])
fig_seasonal.update_yaxes(autorange=True)
fig_seasonal.update_layout(
    height=800,
    width=1200,
    template="plotly",
    title={'x': 0.5, 'xanchor': 'center'},
    showlegend=False,
    margin=dict(l=50, r=50, t=50, b=50)
)
fig_seasonal.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
fig_seasonal.show()

# (B) Gráfico de la componente de tendencia
fig_trend = px.line(
    df_decomp,
    x="periodo",
    y="trend",
    facet_row="product_id",
    title="Componente de Tendencia por Producto",
    labels={"trend": "Tendencia", "periodo": "Periodo"}
)
fig_trend.update_xaxes(range=[start_date, end_date])
fig_trend.update_yaxes(autorange=True)
fig_trend.update_layout(
    height=800,
    width=1200,
    template="plotly",
    title={'x': 0.5, 'xanchor': 'center'},
    showlegend=False,
    margin=dict(l=50, r=50, t=50, b=50)
)
fig_trend.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
fig_trend.show()

# (C) Gráfico de la componente de ruido (residuos)
fig_resid = px.line(
    df_decomp,
    x="periodo",
    y="resid",
    facet_row="product_id",
    title="Componente de Ruido (Residuos) por Producto",
    labels={"resid": "Ruido", "periodo": "Periodo"}
)
fig_resid.update_xaxes(range=[start_date, end_date])
fig_resid.update_yaxes(autorange=True)
fig_resid.update_layout(
    height=800,
    width=1200,
    template="plotly",
    title={'x': 0.5, 'xanchor': 'center'},
    showlegend=False,
    margin=dict(l=50, r=50, t=50, b=50)
)
fig_resid.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
fig_resid.show()

# Modelados con Auto Arima

In [ ]:
%pip install statsforecast

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 354.4/354.4 kB 8.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 285.8/285.8 kB 20.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 278.2/278.2 kB 18.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.2/42.2 kB 2.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.3/62.3 kB 3.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 135.3/135.3 kB 11.8 MB/s eta 0:00:00


In [ ]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.io as pio
from statsforecast.models import AutoARIMA  # Importa AutoARIMA de nixtla/statsforecast
from datetime import datetime

# Configurar el template por defecto para evitar heredar configuraciones anteriores.
pio.templates.default = "plotly"

# =====================================================
# Paso 1: Preparar la serie de cada producto (global)
# =====================================================
# Filtrar el período 2017-01 a 2019-12.
start_date = pd.to_datetime('2017-01-01')
end_date   = pd.to_datetime('2019-12-31')
df_filtered = all_chunk_depurado_df[
    (all_chunk_depurado_df['periodo'] >= start_date) &
    (all_chunk_depurado_df['periodo'] <= end_date)
].copy()

# Agrupar por producto y mes (sumando ventas de todos los clientes).
df_prod = df_filtered.groupby(['product_id', 'periodo'])['tn'].sum().reset_index()

# Completar la serie: crear todas las combinaciones de producto y mes, rellenando con 0 donde falte.
all_months = pd.date_range(start=start_date, end=end_date, freq='MS')
# Seleccionar, por ejemplo, los primeros 10 productos.
unique_products = sorted(df_prod['product_id'].unique())[:10]

all_combinations = pd.MultiIndex.from_product(
    [unique_products, all_months],
    names=['product_id', 'periodo']
).to_frame(index=False)
df_series = pd.merge(all_combinations, df_prod, on=['product_id', 'periodo'], how='left')
df_series['tn'] = df_series['tn'].fillna(0)

# Convertir la serie para cada producto en un diccionario (guardando fechas y valores).
series_dict = {}
for prod, group in df_series.groupby('product_id'):
    group_sorted = group.sort_values('periodo')
    series_dict[prod] = {
        "dates": group_sorted['periodo'].tolist(),
        "values": group_sorted['tn'].tolist()
    }

# =====================================================
# Paso 2: Fase 1 – Entrenamiento hasta 2019-10 y pronóstico para 2019-12
# =====================================================
forecast_results_phase1 = {}  # Pronóstico para 2019-12 por producto.
error_results_phase1 = {}     # Error absoluto del forecast para cada producto.

train_end_phase1 = pd.to_datetime('2019-10-01')  # Entrenar la serie hasta 2019-10.

for prod, series_data in series_dict.items():
    dates = series_data["dates"]
    values = series_data["values"]
    s_df = pd.DataFrame({"periodo": dates, "tn": values})
    s_df = s_df.sort_values("periodo")
    s_train = s_df[s_df["periodo"] <= train_end_phase1]

    if len(s_train) < 24:
        print(f"Producto {prod}: serie demasiado corta para fase 1.")
        continue

    # Entrenar el modelo AutoARIMA usando la serie de entrenamiento convertida a un array NumPy.
    model = AutoARIMA(season_length=12)
    model.fit(s_train["tn"].values)

    # Pronosticar 2 períodos adelante (2019-11 y 2019-12).
    forecast = model.predict(h=2)
    # Si forecast es un dict, extraer la clave "mean"
    if isinstance(forecast, dict):
        forecast = forecast.get("mean")
    fc = np.atleast_1d(forecast)
    if fc.size >= 2:
        forecast_2019_12 = fc[1]
    else:
        forecast_2019_12 = fc[0]
    forecast_results_phase1[prod] = forecast_2019_12

    # Obtener el valor real para 2019-12.
    try:
        real_2019_12 = s_df[s_df["periodo"] == pd.to_datetime('2019-12-01')]["tn"].iloc[0]
    except IndexError:
        real_2019_12 = np.nan

    error = np.abs(real_2019_12 - forecast_2019_12)
    error_results_phase1[prod] = error

    # Graficar la serie real (hasta 2019-12) y marcar el forecast en 2019-12-01.
    fig = px.line(s_df, x="periodo", y="tn",
                  title=f'Producto {prod} – Fase 1: Pronóstico para 2019-12',
                  labels={"tn": "Ventas (tn)", "periodo": "Periodo"})
    fig.add_scatter(x=[pd.to_datetime('2019-12-01')], y=[forecast_2019_12],
                    mode='markers', marker=dict(color='red', size=10),
                    name='Forecast 2019-12')
    fig.add_scatter(x=[pd.to_datetime('2019-12-01')], y=[real_2019_12],
                    mode='markers', marker=dict(color='green', size=10),
                    name='Real 2019-12')
    fig.update_layout(template="plotly")
    fig.show()

total_forecast_error_phase1 = sum(error_results_phase1.values())
print("Total Forecast Error Fase 1 (acumulado):", total_forecast_error_phase1)

# =====================================================
# Paso 3: Fase 2 – Entrenamiento hasta 2019-12 y pronóstico para 2020-02
# =====================================================
forecast_results_phase2 = {}

train_end_phase2 = pd.to_datetime('2019-12-01')  # Entrenar la serie hasta 2019-12.

for prod, series_data in series_dict.items():
    dates = series_data["dates"]
    values = series_data["values"]
    s_df = pd.DataFrame({"periodo": dates, "tn": values})
    s_df = s_df.sort_values("periodo")
    s_train = s_df[s_df["periodo"] <= train_end_phase2]

    if len(s_train) < 24:
        print(f"Producto {prod}: serie demasiado corta para fase 2.")
        continue

    model = AutoARIMA(season_length=12)
    model.fit(s_train["tn"].values)
    # Pronosticar 2 períodos adelante (2020-01 y 2020-02).
    forecast = model.predict(h=2)
    if isinstance(forecast, dict):
        forecast = forecast.get("mean")
    fc = np.atleast_1d(forecast)
    if fc.size >= 2:
        forecast_2020_02 = fc[1]
    else:
        forecast_2020_02 = fc[0]
    forecast_results_phase2[prod] = forecast_2020_02

    # Graficar la serie (hasta 2019-12) y marcar el forecast para 2020-02 (se asigna a 2020-02-01).
    fig = px.line(s_df, x="periodo", y="tn",
                  title=f'Producto {prod} – Fase 2: Pronóstico para 2020-02',
                  labels={"tn": "Ventas (tn)", "periodo": "Periodo"})
    fig.add_scatter(x=[pd.to_datetime('2020-02-01')], y=[forecast_2020_02],
                    mode='markers', marker=dict(color='red', size=10),
                    name='Forecast 2020-02')
    fig.update_layout(template="plotly")
    fig.show()

# =====================================================
# Paso 4: Guardar los pronósticos de 2020-02 en un archivo CSV.
# =====================================================
df_forecasts_phase2 = pd.DataFrame({
    'product_id': list(forecast_results_phase2.keys()),
    'tn': list(forecast_results_phase2.values())
})
df_forecasts_phase2.to_csv("forecast_2020_02.csv", index=False, encoding="utf-8")
print("Se ha guardado el archivo forecast_2020_02.csv con los pronósticos de cada producto.")

Total Forecast Error Fase 1 (acumulado): 1352.3069651319006


Se ha guardado el archivo forecast_2020_02.csv con los pronósticos de cada producto.


# Ahora para todos los productos

In [ ]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.io as pio
from statsforecast.models import AutoARIMA  # AutoARIMA de nixtla/statsforecast
from datetime import datetime

# ------------------------------------------------------------
# Configuración inicial: usar el template "plotly" por defecto.
pio.templates.default = "plotly"

# ------------------------------------------------------------
# Paso 1. Preparar la serie histórica para productos a predecir
# ------------------------------------------------------------
# Se filtra el histórico para el período 2017-01 a 2019-12
start_date = pd.to_datetime('2017-01-01')
end_date   = pd.to_datetime('2019-12-31')
df_filtered = all_chunk_depurado_df[
    (all_chunk_depurado_df['periodo'] >= start_date) &
    (all_chunk_depurado_df['periodo'] <= end_date)
].copy()

# Agrupar por producto y mes (suma de ventas de todos los clientes)
df_prod = df_filtered.groupby(['product_id', 'periodo'])['tn'].sum().reset_index()

# Restricción: Sólo trabajamos con los productos del dataset productos_a_predecir_df.
# Se asume que el código de producto está en la columna "product_id"
predicted_products = sorted(productos_a_predecir_df['product_id'].unique())

# Filtramos los datos históricos para quedarnos solo con los productos a predecir
df_prod = df_prod[df_prod['product_id'].isin(predicted_products)]

# Completar la serie: Para cada producto, aseguramos que exista registro para cada mes.
all_months = pd.date_range(start=start_date, end=end_date, freq='MS')
all_combinations = pd.MultiIndex.from_product(
    [predicted_products, all_months],
    names=['product_id', 'periodo']
).to_frame(index=False)
df_series = pd.merge(all_combinations, df_prod, on=['product_id', 'periodo'], how='left')
df_series['tn'] = df_series['tn'].fillna(0)

# Creamos un diccionario con la serie completa para cada producto:
series_dict = {}
for prod, group in df_series.groupby('product_id'):
    group_sorted = group.sort_values('periodo')
    series_dict[prod] = {
        "dates": group_sorted['periodo'].tolist(),
        "values": group_sorted['tn'].tolist()
    }

# ------------------------------------------------------------
# Paso 2. Fase 1 – Predicción para 2019-12 (Entrenar hasta 2019-10)
# ------------------------------------------------------------
forecast_results_phase1 = {}  # Almacenará los forecast para 2019-12
error_results_phase1 = {}     # Almacenará el error absoluto de cada forecast

train_end_phase1 = pd.to_datetime('2019-10-01')  # Usamos datos hasta octubre de 2019

# Para efectos de graficación, definimos los primeros 5 productos a mostrar:
products_to_plot = sorted(predicted_products)[:5]

for prod, series_data in series_dict.items():
    dates = series_data["dates"]
    values = series_data["values"]
    s_df = pd.DataFrame({"periodo": dates, "tn": values})
    s_df = s_df.sort_values("periodo")

    # Seleccionar datos de entrenamiento hasta 2019-10
    s_train = s_df[s_df["periodo"] <= train_end_phase1]

    if len(s_train) < 24:
        print(f"Producto {prod}: serie demasiado corta para fase 1.")
        continue

    # Entrenar el modelo AutoARIMA (se usa season_length=12 para datos mensuales)
    model = AutoARIMA(season_length=12)
    model.fit(s_train["tn"].values)

    # Pronosticar 2 períodos adelante (2019-11 y 2019-12)
    forecast = model.predict(h=2)
    # Si el resultado es un dict (por ejemplo, {'mean': [...]}) extraemos la clave "mean"
    if isinstance(forecast, dict):
        forecast = forecast.get("mean")
    fc = np.atleast_1d(forecast)
    # Verificamos que se tenga, en lo ideal, dos períodos; si no, usamos el único valor.
    if fc.size >= 2:
        forecast_2019_12 = fc[1]
    else:
        forecast_2019_12 = fc[0]
    forecast_results_phase1[prod] = forecast_2019_12

    # Extraer el valor real para 2019-12
    try:
        real_2019_12 = s_df[s_df["periodo"] == pd.to_datetime('2019-12-01')]["tn"].iloc[0]
    except IndexError:
        real_2019_12 = np.nan

    error = np.abs(real_2019_12 - forecast_2019_12)
    error_results_phase1[prod] = error

    # Graficar únicamente si el producto está entre los primeros 5 a predecir
    if prod in products_to_plot:
        fig = px.line(s_df, x="periodo", y="tn",
                      title=f'Producto {prod} – Fase 1: Pronóstico para 2019-12',
                      labels={"tn": "Ventas (tn)", "periodo": "Periodo"})
        fig.add_scatter(x=[pd.to_datetime('2019-12-01')], y=[forecast_2019_12],
                        mode='markers', marker=dict(color='red', size=10),
                        name='Forecast 2019-12')
        fig.add_scatter(x=[pd.to_datetime('2019-12-01')], y=[real_2019_12],
                        mode='markers', marker=dict(color='green', size=10),
                        name='Real 2019-12')
        fig.update_layout(template="plotly")
        fig.show()

total_forecast_error_phase1 = sum(error_results_phase1.values())
print("Total Forecast Error Fase 1 (acumulado):", total_forecast_error_phase1)

# ------------------------------------------------------------
# Paso 3. Fase 2 – Predicción para 2020-02 (Entrenar hasta 2019-12)
# ------------------------------------------------------------
forecast_results_phase2 = {}

train_end_phase2 = pd.to_datetime('2019-12-01')  # Usamos datos hasta diciembre de 2019

for prod, series_data in series_dict.items():
    dates = series_data["dates"]
    values = series_data["values"]
    s_df = pd.DataFrame({"periodo": dates, "tn": values})
    s_df = s_df.sort_values("periodo")

    # Seleccionar datos de entrenamiento hasta 2019-12
    s_train = s_df[s_df["periodo"] <= train_end_phase2]

    if len(s_train) < 24:
        print(f"Producto {prod}: serie demasiado corta para fase 2.")
        continue

    model = AutoARIMA(season_length=12)
    model.fit(s_train["tn"].values)
    # Pronosticar 2 períodos adelante (2020-01 y 2020-02)
    forecast = model.predict(h=2)
    if isinstance(forecast, dict):
        forecast = forecast.get("mean")
    fc = np.atleast_1d(forecast)
    if fc.size >= 2:
        forecast_2020_02 = fc[1]
    else:
        forecast_2020_02 = fc[0]
    forecast_results_phase2[prod] = forecast_2020_02

    # Graficar únicamente para los primeros 5 productos
    if prod in products_to_plot:
        fig = px.line(s_df, x="periodo", y="tn",
                      title=f'Producto {prod} – Fase 2: Pronóstico para 2020-02',
                      labels={"tn": "Ventas (tn)", "periodo": "Periodo"})
        fig.add_scatter(x=[pd.to_datetime('2020-02-01')], y=[forecast_2020_02],
                        mode='markers', marker=dict(color='red', size=10),
                        name='Forecast 2020-02')
        fig.update_layout(template="plotly")
        fig.show()

# ------------------------------------------------------------
# Paso 4. Guardar los pronósticos de 2020-02 para TODOS los productos
# ------------------------------------------------------------
df_forecasts_phase2 = pd.DataFrame({
    'product_id': list(forecast_results_phase2.keys()),
    'tn': list(forecast_results_phase2.values())
})
df_forecasts_phase2.to_csv("forecast_2020_02.csv", index=False, encoding="utf-8")
print("Se ha guardado el archivo forecast_2020_02.csv con los pronósticos de cada producto.")

Total Forecast Error Fase 1 (acumulado): 8598.534511843782


Se ha guardado el archivo forecast_2020_02.csv con los pronósticos de cada producto.


# volver a empezar, ahora exportando a pdf

In [ ]:
%pip install PyPDF2 kaleido
!pip install -U kaleido

In [ ]:
import os
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.io as pio
from statsforecast.models import AutoARIMA  # AutoARIMA de nixtla/statsforecast
from datetime import datetime
from PyPDF2 import PdfMerger

# ------------------------------------------------------------
# Configuración inicial
# ------------------------------------------------------------
pio.templates.default = "plotly"  # Usar el template por defecto

# ------------------------------------------------------------
# Paso 1. Preparar la serie histórica para los productos a predecir
# ------------------------------------------------------------
# Se asume que:
# - all_chunk_depurado_df es el DataFrame histórico con columnas:
#    "product_id", "periodo" (datetime) y "tn" (ventas en toneladas)
# - productos_a_predecir_df es el DataFrame con la columna "product_id"
#   que indica los productos para los que se quiere predecir.

start_date = pd.to_datetime('2017-01-01')
end_date   = pd.to_datetime('2019-12-31')

df_filtered = all_chunk_depurado_df[
    (all_chunk_depurado_df['periodo'] >= start_date) &
    (all_chunk_depurado_df['periodo'] <= end_date)
].copy()

# Agrupar por producto y mes (sumando todas las ventas)
df_prod = df_filtered.groupby(['product_id', 'periodo'])['tn'].sum().reset_index()

# Filtrar solo los productos a predecir:
predicted_products = sorted(productos_a_predecir_df['product_id'].unique())
df_prod = df_prod[df_prod['product_id'].isin(predicted_products)]

# Completamos la serie para que cada producto tenga datos de todos los meses en el rango.
all_months = pd.date_range(start=start_date, end=end_date, freq='MS')
all_combinations = pd.MultiIndex.from_product(
    [predicted_products, all_months],
    names=['product_id', 'periodo']
).to_frame(index=False)
df_series = pd.merge(all_combinations, df_prod, on=['product_id', 'periodo'], how='left')
df_series['tn'] = df_series['tn'].fillna(0)

# Crear un diccionario de series: para cada producto guardamos una lista de fechas y de valores.
series_dict = {}
for prod, group in df_series.groupby('product_id'):
    group_sorted = group.sort_values('periodo')
    series_dict[prod] = {
        "dates": group_sorted['periodo'].tolist(),
        "values": group_sorted['tn'].tolist()
    }

# ------------------------------------------------------------
# Paso 2. Fase 1 – Predicción para 2019-12 (Entrenar hasta 2019-10)
# ------------------------------------------------------------
forecast_results_phase1 = {}  # Forecast para 2019-12 por producto
error_results_phase1 = {}     # Error absoluto para cada producto (para diciembre 2019)
sum_abs_error = 0.0           # Acumulador para la suma de errores absolutos
sum_real = 0.0                # Acumulador para la suma de ventas reales en diciembre 2019

train_end_phase1 = pd.to_datetime('2019-10-01')  # Entrenar hasta octubre 2019

# Directorio para guardar los gráficos de fase 1
phase1_dir = "phase1_plots"
os.makedirs(phase1_dir, exist_ok=True)
phase1_pdf_files = []

for prod, series_data in series_dict.items():
    dates = series_data["dates"]
    values = series_data["values"]
    s_df = pd.DataFrame({"periodo": dates, "tn": values}).sort_values("periodo")
    s_train = s_df[s_df["periodo"] <= train_end_phase1]

    if len(s_train) < 24:
        print(f"Producto {prod}: serie demasiado corta para fase 1.")
        continue

    # Entrenar AutoARIMA con season_length=12
    model = AutoARIMA(season_length=12)
    model.fit(s_train["tn"].values)

    # Pronosticar 2 períodos adelante (2019-11 y 2019-12)
    forecast = model.predict(h=2)
    if isinstance(forecast, dict):
        forecast = forecast.get("mean")
    fc = np.atleast_1d(forecast)
    if fc.size >= 2:
        forecast_2019_12 = fc[1]
    else:
        forecast_2019_12 = fc[0]
    forecast_results_phase1[prod] = forecast_2019_12

    # Extraer el valor real para 2019-12
    try:
        real_2019_12 = s_df[s_df["periodo"] == pd.to_datetime('2019-12-01')]["tn"].iloc[0]
    except IndexError:
        real_2019_12 = np.nan

    abs_error = np.abs(real_2019_12 - forecast_2019_12)
    error_results_phase1[prod] = abs_error
    sum_abs_error += abs_error
    sum_real += real_2019_12

    # Generar el gráfico de la serie y marcar el forecast – se guarda individualmente para cada producto
    fig = px.line(s_df, x="periodo", y="tn",
                  title=f'Producto {prod} – Fase 1: Pronóstico para 2019-12',
                  labels={"tn": "Ventas (tn)", "periodo": "Periodo"})
    fig.add_scatter(x=[pd.to_datetime('2019-12-01')], y=[forecast_2019_12],
                    mode='markers', marker=dict(color='red', size=10),
                    name='Forecast 2019-12')
    fig.add_scatter(x=[pd.to_datetime('2019-12-01')], y=[real_2019_12],
                    mode='markers', marker=dict(color='green', size=10),
                    name='Real 2019-12')
    fig.update_layout(template="plotly")
    # Guardar el gráfico en PDF (archivo individual)
    pdf_path = os.path.join(phase1_dir, f"prod_{prod}_phase1.pdf")
    fig.write_image(pdf_path)
    phase1_pdf_files.append(pdf_path)

# Calcular Total Forecast Error (TFE) para fase 1:
# TFE = sum_{i} |Real_i - Forecast_i| / sum_{i} (Real_i)
if sum_real > 0:
    TFE_phase1 = sum_abs_error / sum_real
else:
    TFE_phase1 = np.nan
print("Total Forecast Error Fase 1 (TFE):", TFE_phase1)

# Fusionar los 780 gráficos de fase 1 en un único PDF (un archivo de varias páginas)
merger = PdfMerger()
for pdf in phase1_pdf_files:
    merger.append(pdf)
merged_phase1_pdf_path = "Fase1_All_Products.pdf"
merger.write(merged_phase1_pdf_path)
merger.close()
print("Se ha guardado el archivo", merged_phase1_pdf_path)

# ------------------------------------------------------------
# Paso 3. Fase 2 – Predicción para 2020-02 (Entrenar hasta 2019-12)
# ------------------------------------------------------------
forecast_results_phase2 = {}
train_end_phase2 = pd.to_datetime('2019-12-01')  # Entrenar hasta diciembre 2019

# Directorio para guardar los gráficos de fase 2
phase2_dir = "phase2_plots"
os.makedirs(phase2_dir, exist_ok=True)
phase2_pdf_files = []

for prod, series_data in series_dict.items():
    dates = series_data["dates"]
    values = series_data["values"]
    s_df = pd.DataFrame({"periodo": dates, "tn": values}).sort_values("periodo")
    s_train = s_df[s_df["periodo"] <= train_end_phase2]

    if len(s_train) < 24:
        print(f"Producto {prod}: serie demasiado corta para fase 2.")
        continue

    model = AutoARIMA(season_length=12)
    model.fit(s_train["tn"].values)
    # Pronosticar 2 períodos adelante (2020-01 y 2020-02)
    forecast = model.predict(h=2)
    if isinstance(forecast, dict):
        forecast = forecast.get("mean")
    fc = np.atleast_1d(forecast)
    if fc.size >= 2:
        forecast_2020_02 = fc[1]
    else:
        forecast_2020_02 = fc[0]
    forecast_results_phase2[prod] = forecast_2020_02

    # Generar el gráfico para la fase 2 para este producto
    fig = px.line(s_df, x="periodo", y="tn",
                  title=f'Producto {prod} – Fase 2: Pronóstico para 2020-02',
                  labels={"tn": "Ventas (tn)", "periodo": "Periodo"})
    fig.add_scatter(x=[pd.to_datetime('2020-02-01')], y=[forecast_2020_02],
                    mode='markers', marker=dict(color='red', size=10),
                    name='Forecast 2020-02')
    fig.update_layout(template="plotly")
    pdf_path = os.path.join(phase2_dir, f"prod_{prod}_phase2.pdf")
    fig.write_image(pdf_path)
    phase2_pdf_files.append(pdf_path)

# Fusionar los PDF de fase 2 en un único archivo
merger = PdfMerger()
for pdf in phase2_pdf_files:
    merger.append(pdf)
merged_phase2_pdf_path = "Fase2_All_Products.pdf"
merger.write(merged_phase2_pdf_path)
merger.close()
print("Se ha guardado el archivo", merged_phase2_pdf_path)

# ------------------------------------------------------------
# Paso 4. Guardar los pronósticos de 2020-02 en un archivo CSV
# ------------------------------------------------------------
df_forecasts_phase2 = pd.DataFrame({
    'product_id': list(forecast_results_phase2.keys()),
    'tn': list(forecast_results_phase2.values())
})
df_forecasts_phase2.to_csv("forecast_2020_02.csv", index=False, encoding="utf-8")
print("Se ha guardado el archivo forecast_2020_02.csv con los pronósticos de cada producto.")

Total Forecast Error Fase 1 (TFE): 0.34195459582140575
Se ha guardado el archivo Fase1_All_Products.pdf
Se ha guardado el archivo Fase2_All_Products.pdf
Se ha guardado el archivo forecast_2020_02.csv con los pronósticos de cada producto.


# Entrenamiento en granularidad cliente producto

In [ ]:
pip install statsforecast plotly tqdm kaleido PyPDF2

In [ ]:
import os
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.io as pio
from statsforecast.models import AutoARIMA
from datetime import datetime
from PyPDF2 import PdfMerger
from tqdm import tqdm  # Para mostrar progreso

# Configuración de Plotly
pio.templates.default = "plotly"

# ------------------------------------------------------------------------------
# Paso 1. Preparar la serie a nivel producto–customer
# ------------------------------------------------------------------------------
start_date = pd.to_datetime('2017-01-01')
end_date   = pd.to_datetime('2019-12-31')

df_filtered = all_chunk_depurado_df[
    (all_chunk_depurado_df['periodo'] >= start_date) &
    (all_chunk_depurado_df['periodo'] <= end_date)
].copy()

# Agrupar por producto, customer y mes
df_customer = df_filtered.groupby(['product_id', 'customer_id', 'periodo'])['tn'].sum().reset_index()

# Filtrar productos a predecir
predicted_products = sorted(productos_a_predecir_df['product_id'].unique())
df_customer = df_customer[df_customer['product_id'].isin(predicted_products)]

# Completar la serie para cada combinación producto–customer
all_months = pd.date_range(start=start_date, end=end_date, freq='MS')
prod_customer = df_customer[['product_id', 'customer_id']].drop_duplicates()
all_combinations = prod_customer.assign(key=1).merge(
    pd.DataFrame({'periodo': all_months, 'key': 1}), on='key').drop('key', axis=1)
df_customer_series = pd.merge(all_combinations, df_customer, on=['product_id', 'customer_id', 'periodo'], how='left')
df_customer_series['tn'] = df_customer_series['tn'].fillna(0)

# Diccionario de series por producto–customer
customer_series_dict = {}
for (prod, cust), group in df_customer_series.groupby(['product_id', 'customer_id']):
    group_sorted = group.sort_values('periodo')
    customer_series_dict[(prod, cust)] = {
        "dates": group_sorted['periodo'].tolist(),
        "values": group_sorted['tn'].tolist()
    }

# ------------------------------------------------------------------------------
# Paso 2. Entrenamiento a nivel producto–customer
# ------------------------------------------------------------------------------
forecast_phase1 = {}
actual_phase1 = {}
forecast_phase2 = {}

train_end_phase1 = pd.to_datetime('2019-10-01')
train_end_phase2 = pd.to_datetime('2019-12-01')

print("Entrenando modelos...")
for key in tqdm(customer_series_dict.keys(), desc="Entrenamiento"):
    prod, cust = key
    series_data = customer_series_dict[key]
    dates = series_data["dates"]
    values = series_data["values"]
    s_df = pd.DataFrame({"periodo": dates, "tn": values}).sort_values("periodo")

    if len(s_df) < 24:
        continue

    # Fase 1: Entrenar hasta 2019-10 y predecir 2019-12
    s_train1 = s_df[s_df["periodo"] <= train_end_phase1]
    model1 = AutoARIMA(season_length=12)
    model1.fit(s_train1["tn"].values)
    forecast1 = model1.predict(h=2)
    if isinstance(forecast1, dict):
        forecast1 = forecast1.get("mean")
    fc1 = np.atleast_1d(forecast1)
    forecast_phase1[key] = fc1[1] if fc1.size >= 2 else fc1[0]
    try:
        actual_phase1[key] = s_df[s_df["periodo"] == pd.to_datetime("2019-12-01")]["tn"].iloc[0]
    except IndexError:
        actual_phase1[key] = np.nan

    # Fase 2: Entrenar hasta 2019-12 y predecir 2020-02
    s_train2 = s_df[s_df["periodo"] <= train_end_phase2]
    model2 = AutoARIMA(season_length=12)
    model2.fit(s_train2["tn"].values)
    forecast2 = model2.predict(h=2)
    if isinstance(forecast2, dict):
        forecast2 = forecast2.get("mean")
    fc2 = np.atleast_1d(forecast2)
    forecast_phase2[key] = fc2[1] if fc2.size >= 2 else fc2[0]

# ------------------------------------------------------------------------------
# Paso 3. Generación de gráficos
# ------------------------------------------------------------------------------
phase1_dir = "phase1_customer_plots"
phase2_dir = "phase2_customer_plots"
os.makedirs(phase1_dir, exist_ok=True)
os.makedirs(phase2_dir, exist_ok=True)

phase1_pdf_files = []
phase2_pdf_files = []

print("Generando gráficos y guardando en PDF...")
for key in tqdm(customer_series_dict.keys(), desc="Generación de gráficos"):
    prod, cust = key
    series_data = customer_series_dict[key]
    dates = series_data["dates"]
    values = series_data["values"]
    s_df = pd.DataFrame({"periodo": dates, "tn": values}).sort_values("periodo")

    # Fase 1
    if key in forecast_phase1:
        fc_val = forecast_phase1[key]
        real_val = actual_phase1.get(key, np.nan)
        fig1 = px.line(s_df, x="periodo", y="tn", title=f"Producto {prod} - Customer {cust} – Fase 1")
        fig1.add_scatter(x=[pd.to_datetime("2019-12-01")], y=[fc_val], mode="markers", marker=dict(color="red", size=10))
        fig1.write_image(f"{phase1_dir}/prod_{prod}_cust_{cust}_phase1.pdf")
        phase1_pdf_files.append(f"{phase1_dir}/prod_{prod}_cust_{cust}_phase1.pdf")

# Fusión en un único documento PDF
merger1 = PdfMerger()
for pdf in phase1_pdf_files:
    merger1.append(pdf)
merger1.write("Customer_Level_Fase1_All.pdf")
merger1.close()
print("Se ha guardado el PDF de Fase 1.")

In [ ]:
# ------------------------------------------------------------------------------
# Fase 2: Generación de gráficos y guardado en PDF
# ------------------------------------------------------------------------------
print("Generando gráficos de la Fase 2 y guardando en PDF...")
for key in tqdm(customer_series_dict.keys(), desc="Generación de gráficos Fase 2"):
    prod, cust = key
    series_data = customer_series_dict[key]
    dates = series_data["dates"]
    values = series_data["values"]
    s_df = pd.DataFrame({"periodo": dates, "tn": values}).sort_values("periodo")

    # Fase 2: Pronóstico para 2020-02
    if key in forecast_phase2:
        fc_val2 = forecast_phase2[key]
        fig2 = px.line(s_df, x="periodo", y="tn",
                       title=f"Producto {prod} - Customer {cust} – Fase 2: Pronóstico para 2020-02",
                       labels={"tn": "Ventas (tn)", "periodo": "Periodo"})
        fig2.add_scatter(x=[pd.to_datetime("2020-02-01")], y=[fc_val2],
                         mode="markers", marker=dict(color="red", size=10),
                         name="Forecast 2020-02")
        fig2.update_layout(template="plotly")
        pdf_path2 = os.path.join(phase2_dir, f"prod_{prod}_cust_{cust}_phase2.pdf")
        fig2.write_image(pdf_path2)
        phase2_pdf_files.append(pdf_path2)

# Fusionar todos los PDFs individuales de la Fase 2 en un único archivo PDF
merger2 = PdfMerger()
for pdf in phase2_pdf_files:
    merger2.append(pdf)
merged_phase2_customer_pdf = "Customer_Level_Fase2_All.pdf"
merger2.write(merged_phase2_customer_pdf)
merger2.close()
print("Se ha guardado el PDF de Fase 2 a nivel customer:", merged_phase2_customer_pdf)